# AST416 Astronomide Sayısal Çözümleme - II #
## Ders - 03 İnterpolasyon ##

Doç. Dr. Özgür Baştürk <br>
Ankara Üniversitesi, Astronomi ve Uzay Bilimleri Bölümü <br>
obasturk at ankara.edu.tr <br>
http://ozgur.astrotux.org

# Bu derste neler öğreneceksiniz?#
## İnterpolasyon ##

* [İnterpolasyon](#İnterpolasyon)
* [scipy.Interpolate Modülü ile İnterpolasyon](#scipy.Interpolate-Modülü-ile-İnterpolasyon)
    * [1 Boyutlu İnterpolasyon: interp1d](#1-Boyutlu-İnterpolasyon:-interp1d)
    * [Çok Boyutlu İnterpolasyon: griddata](#Çok-Boyutlu-İnterpolasyon:-griddata)
* [Yapısal Spline İnterpolasyonu](#Yapısal-Spline-İnterpolasyonu)
    * [Bir Boyutlu Yapısal Spline İnterpolasyonu](#Bir-Boyutlu-Yapısal-Spline-İnterpolasyonu)
    * [İki Boyutlu Yapısal Spline İnterpolasyonu](#İki-Boyutlu-Yapısal-Spline-İnterpolasyonu)
* [UnivariateSpline İle Nesne Yönelimli Spline İnterpolasyonu](#UnivariateSpline-İle-Nesne-Yönelimli-Spline-İnterpolasyonu)
* [Örnek: Spline Fonksiyonları ile İnterpolasyon](#Örnek:-Spline-Fonksiyonları-ile-İnterpolasyon)
* [Ödev 3](#Ödev-3)
* [Kaynaklar](#Kaynaklar)

# İnterpolasyon #

Sayısal çözümlemede interpolasyon formal olarak bir süreksiz veride bilinen değerlerden yola çıkarak bilinmeyen ara değerlerin hesaplanmasına dayanan her türlü yöntem olarak tanımlanır. Astronomi, interpolasyonun en sık ihtiyaç duyulduğu alanlardan biridir. Zira astronomide sürekli veri almak ancak uzay teleskoplarıyla mümkün olabilmekte, onlarda dahi sürekli veri alınmasına engel kısıtlar bulunmaktadır. Gece / gündüz, kapalı / açık hava, aletsel problemler, kullanılan dedektörlerin veri alabilme sıklığı, çok bant gözlem yapma ihtiyacı gibi nedenlerle astronomide kullanılan verinin içerisinde büyük boşluklar oluşabilmektedir. Bu boşlukları, var olan veriden yola çıkarak doldurmak önemli bir ihtiyaç olarak karşımıza çıkmaktadır.

İnterpolasyonda izlenen geleneksel yöntemler, örneklerle birlikte [<i>İnterpolasyon Yöntemleri</i>](http://ozgur.astrotux.org/ast416/Ders_03/Ders03_Interpolasyon_Yontemleri.pdf) kaynağında verilmiştir. Ayrıca astronoimde en sık başvurulan interpolasyon yöntemi olan [</i>Spline İnterpolasyonu</i>](http://ozgur.astrotux.org/ast416/Ders_03/Ders03_Spline_Interpolasyonu.pdf) dokümanında ayrıntılı olarak anlatılmş ve örneklendirilmiştir. Bu derste Python programlama dilinin ve ek modüllerin interpolasyona ilişkin sağladığı olanaklar örnek kodlarla işlenecektir. Dersten önce bu iki dokümanın incelenmesinde fayda vardır.

# scipy.Interpolate Modülü ile İnterpolasyon #

## 1 Boyutlu İnterpolasyon: interp1d  ##

`scipy.interpolate` modülü fonksiyonlarından `interp1d` verilen verideki her bir $(x,y)$ ikilisinin arasına bir doğru uyumlayarak, istenen $x$ değerleri için bu doğrularda karşılık geldiği $y$ değerlerini hesaplayarak interpolasyon yapar.

Aşağıdaki örnekte ilk olarak $y = e^{\frac{-x}{3}}$ fonksiyonu $x = [0,10)$ aralığında 50 nokta için oluşturulmaktadır. Daha sonra bu $x,y$ ikilileri `interpolate.interp1d` fonksiyonuna sağlanarak $f$ doğrusal interpolasyon fonksiyonu oluşturulmuş ve $x_{yeni} = [1,8]$ aralığında oluşturulan 5 yeni x değeri bu fonksiyona sağlanarak, bu noktalar için $y_{yeni}$ interpolasyon değerleri elde edilmiştir. Bu interpolasyon değerleri ve $(x,y)$ ikilileri arasında interpolasyonun yapıldığı doğrular orjinal fonksiyonla birlikte çizdirilmiştir.

In [ ]:
import matplotlib.pyplot as plt
import numpy as np
from scipy import interpolate
x = np.arange(0,10)
y = np.exp(-x/3.0) # y = e^(-x / 3)
f = interpolate.interp1d(x,y)
xyeni =  np.linspace(1,8,5)
yyeni = f(xyeni)
plt.plot(x,y,'b-')
plt.plot(xyeni,yyeni,'ro')
plt.plot(xyeni,yyeni,'r-')
plt.xlabel("x")
plt.ylabel("y")
plt.show()

Aksi söyllenmediği takdirde fonksiyon, veri noktaları arasında birer doğru uyumlayacak şekilde oluşturulur. Eğer `kind` parametresi `cubic` şekilde belirlenmişse bu kez noktaların arasına 3. dereceden birer polinom uyarlanır. Bu yapısıyla fonksiyon gerçekte lineer ya da kübik [spline interpolasyonu](http://ozgur.astrotux.org/ast416/Ders_03/Ders03_Spline_Interpolasyonu.pdf) uygulamaktadır.

Aşağıdaki örnekte bu kez önce $y = cos(-x^2 / 9.0)$ fonksiyonu $x = [0,10]$ aralığındaki 11 nokta için oluşturulmakta; daha sonra, ardışık her $(x,y)$ ikilisine sırasıyla doğrusal ve 3. dereceden polinomlar aynı aralıktaki 41 nokta için uyarlanmaktadır. Burada dikkat edilmesi gereken husus, veri setninin tamamına doğrusal ya da 3. dereceden bir polinomun uyarlanmadığı, bu fonksiyonların veri setindeki ardışık ikililerin arasına uyarlandığıdır. 

In [ ]:
from matplotlib import pyplot as plt
import numpy as np
from scipy.interpolate import interp1d
x = np.linspace(0, 10, 11, endpoint=True)
y = np.cos(-x**2/9.0)
f1 = interp1d(x,y)
f2 = interp1d(x,y,kind='cubic')
xyeni = np.linspace(0, 10, 41, endpoint=True)
y1 = f1(xyeni)
y2 = f2(xyeni)
plt.plot(x, y, 'o', xyeni, y1, '-', xyeni, y2, '-.')
plt.legend(['veri', 'dogrusal', 'kubik'], loc = 'best')
plt.plot
plt.show()

Öncelikle sayısal veri içeren (nümerik) sütunlara ilişkin istatistiklerin verildiğini görüyoruz. Ancak öğrencilerin durumuna ilişkin sütunlarla ilgili de istatistiksel bilgi alabiiriz.

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

## Çok Boyutlu İnterpolasyon: griddata ##

`scipy.interpolated` sadece bir boyutta tanımlı $y = f(x)$ yapısındaki veriler için değil çok boyutlu $z = f(x,y,\omega,...)$ şeklindeki veriler için de interpolasyon yapmaya yönelik olanaklar sağlamaktadır. Öncelikle veriyi oluşturmak üzere

$$z = x^{1 - x}~cos(4~\pi~x)~sin(4~\pi~y^2)^2 $$

fonksiyonunu tanımlayalım

In [ ]:
import numpy as np
def fonk(x, y):
    return x*(1-x)*np.cos(4*np.pi*x) * np.sin(4*np.pi*y**2)**2

$z$ fonksiyonunun $[0, 1] x [0, 1]$ gridindeki çok sayıda nokta için interpolasyonunu hesaplamak üzere değerini bu griddeki rastgele 1000 nokta için bildiğimizi varsayalım. Aşağıda `np.random.rand` fonksiyonu ile ortalama değeri $\mu = 0$, standart sapması $\sigma = 1$ olan birer normal dağılımdan oluşturulan $noktalar$ dizisi iki boyutludur ve fonksiyona gönderilen hem $x$, hem de $y$ değerlerini tutmaktadır. Fonksiyon bu ikililer için hesaplanan $z$ değerlerini döndürür ve böylece arasında interpolasyon yapmak istediğimiz $z$ noktaları oluşturulmuş olur.

In [ ]:
noktalar = np.random.rand(1000, 2)
degerler = fonk(noktalar[:,0], noktalar[:,1])

Bu noktalardan hareketle istediğimiz $(x,y)$ ikilileri için bu kez $z_{interp.}$ interpolasyon değerlerini hesaplayalım. Bunun için interpolasyon yapmak istedğimiz $(x,y)$ ikililerini `np.mgrid` fonksiyonuyla $[0,1]$ arasında $x$ ekseninde 100, $y$ ekseninde 200 nokta içerecek şekilde oluşturalım. ve `interpolate.griddata` fonksiyonuna orjinal verimizi içeren $noktalar$ ve $degerler$ dizilerinin yanı sıra, interpolasyon yapılmasını istedğimiz bu $(x,y)$ ikililerini ve interpolasyon yöntemimizi sağlayalım.

In [ ]:
from scipy.interpolate import griddata
grid_x, grid_y = np.mgrid[0:1:100j, 0:1:200j]
grid_z0 = griddata(noktalar, degerler, (grid_x, grid_y), method='nearest')
grid_z1 = griddata(noktalar, degerler, (grid_x, grid_y), method='linear')
grid_z2 = griddata(noktalar, degerler, (grid_x, grid_y), method='cubic')

Son olarak orjinal fonksiyon ve interpolasyonla elde ettiğimiz noktaları bir grafikle görelim.

In [ ]:
import matplotlib.pyplot as plt
%matplotlib inline
plt.subplot(221)
plt.imshow(fonk(grid_x, grid_y).T, extent=(0,1,0,1), origin='lower')
plt.plot(noktalar[:,0], noktalar[:,1], 'k.', ms=1)
plt.title('Veri')
plt.subplot(222)
plt.imshow(grid_z0.T, extent=(0,1,0,1), origin='lower')
plt.title('En Yakin')
plt.subplot(223)
plt.imshow(grid_z1.T, extent=(0,1,0,1), origin='lower')
plt.title('Dogrusal')
plt.subplot(224)
plt.imshow(grid_z2.T, extent=(0,1,0,1), origin='lower')
plt.title('Kubik')
plt.gcf().set_size_inches(6, 6)
plt.show()

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

# Yapısal Spline İnterpolasyonu #

<b>Yapısal (ing. structural) spline interpolasyonu</b> iki adımda gerçekleştirilir: <b>i)</b> verinin spline interpolasyonu ile temsili oluşturulur, <b>ii)</b> istenen noktalarda spline interpolasyonu hesabı yapılır. Spline temsili için gereken katsayılar doğrudan ya da parametrik olarak elde edilebilir. Verinin doğrudan <i>spline temsili</i> (katsayıların hesabı) `splrep` fonksiyonu ile gerçekleştirilir. Fonksiyona verinin $(x,y)$ noktaları geçirilir; fonksiyon $t$: düğüm noktalarını, $c$: katsayıları, $k$: spline derecesini göstermek üzere $(t, c, k)$ demet değişkenini döndürür. Varsayılan spline derecesi kübiktir ancak istenirse $k$ parametresi ile değişitirilebilir. 

N-boyutlu uzayda veri $splprep$ fonksiyonu ile parametrik olarak temsil edilir. Bu fonksiyon tek bir değişken kabul ettiği için N-boyutlu veri N-boyutlu bir dizi ile tanımlanır. Dizilerin uzunluğu verideki nokta sayısını, dizilerin sayısı ise verinin kaç boyut içerdiğini gösterir. Parametre değişkeni $u$ parametresi ile gösterilir ve $[0-1]$ aralığında monotonik artan bir dizidir. Fonksiyon yine spline parametrelerini tutan $(t, c, k)$ demetini ve $u$ parametresini döndürür.

$s$ interpolasyon sırasındaki düzleştirmenin (ing. smoothing) derecesini belirlemek üzere kulanılabilecek bir parametredir. Varsayılan değeri $m$: veri sayısını göstermek üzere $s = m - \sqrt{2m}$ ile verilir. Düzleştirme istenmiyorsa $s = 0$ olduğu belirtilmelidir. 

Spline temsili belirlendikten sonra istenen noktalarda spline interpolasyon (ve türevi ile integrailinin) hesabını yapan fonksiyonlar  $splev$, $splde$, $splint$ fonksiyonlarıdır. 8 ya da daha fazla düğüm içeren kübik spline fonksiyonları için kök hesabı yapan bir de $splroot$ fonksiyonu bulunmaktadır.

## Bir Boyutlu Yapısal Spline İnterpolasyonu ##

Aşağıda  $y = sin(x)$ fonksiyonuyla oluşturulan veri üzerinden bu yöntem kullanılarak yapılan bir kübik interpolasyon örneği verilmiştir. Görüldüğü gibi orjinal verideki $(x,y)$ ikilileri `scipy.interpolate.splev` fonksiyonuna sağlanarak spline temsili oluşturulmakta, bu temsil interpolasyon yapılmak istenen $x_{yeni}$ noktaları ile `scipy.interpolate.splev` fonksiyonuna sağlanmakta ve bu fonksiyon verilen parametrelerle bu interpolasyon işlemini $x_{yeni}$ noktalarında gerçekleştirerek $y_{yeni}$ değerlerini hesaplamaktadır. $[0, 2\pi]$ aralığında sadece $\pi / 4$ aralıkla 6 nokta kullanılarak oluşturulan veri üzerinde dahi kübik interpolasyonun $sin(x)$ fonksiyonunu başarıyla oluşturduğu görülmektedir.

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from scipy import interpolate
x = np.arange(0, 2*np.pi+np.pi/4, 2*np.pi/8)
y = np.sin(x)
tck = interpolate.splrep(x, y, s=0)
xyeni = np.arange(0, 2*np.pi, np.pi/50)
yyeni = interpolate.splev(xyeni, tck, der=0)
plt.figure()
plt.plot(x,y,'g-',label="veri")
plt.plot(xyeni,yyeni,'b-',label="Kubik spline")
plt.legend(loc="upper right")
plt.axis([-0.05, 6.33, -1.05, 1.05])
plt.title('Kubik Spline Interpolasyonu')
plt.show()

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

## İki Boyutlu Yapısal Spline İnterpolasyonu ##

İki boyutlu bir yüzey üzerindeki veri için ara değer hesabı yapmak (interpolasyon) için `interpolate.bsplrep` fonksiyonu kullanılır. Bu fonksiyona tıpkı 1-boyutlu yapısal (procedural) spline interpolasyonunda olduğu gibi $z = f(x,y)$ yüzeyini oluşturan x, y ve z dizileri gönderilir. Fonksiyon $tx, ty, tz$: düğüm noktalarını, $c$: katsayıları, $kx$, $ky$: spline derecesini göstermek üzere $(tx, ty, tz, c, kx, ky)$ demet değişkenini döndürür. Bu demet değişken `interpolate.splev` fonksiyonuna geçirilir ve istenen $(x, y)$ noktaları için interpolasyon (ara değer) hesabı yapılır.

Tıpkı 1-boyutlu spline interpolasyonunda olduğu gibi 2-boyutlu spline interpolasyounda da $s$ parametresi <i>düzleştirme</i> (ing. smoothing) için kullanılır. $s = 0$ düzleştirme yapılmak istenmediği anlamına gelir. $m$: nokta sayısını göstermek üzere varsayılan düzleştirme değeri $s = m - \sqrt{2m}$ 'dir.

In [ ]:
 import numpy as np
from scipy import interpolate
import matplotlib.pyplot as plt
# 20x20 'lik bir grid uzerinde bir fonksiyon tanimlayalim
x, y = np.mgrid[-1:1:20j, -1:1:20j]
z = (x+y) * np.exp(-6.0*(x*x+y*y))
# grafik
plt.figure()
plt.pcolor(x, y, z)
plt.colorbar()
plt.title("Seyrek Orneklenmis Fonksiyon")
plt.show()
# 70x70'lik daha genis bir grid uzerinden interpolasyonla ornekleme
xyeni, yyeni = np.mgrid[-1:1:70j, -1:1:70j]
tck = interpolate.bisplrep(x, y, z, s=0)
zyeni = interpolate.bisplev(xyeni[:,0], yyeni[0,:], tck)
# grafik
plt.figure()
plt.pcolor(xyeni, yyeni, zyeni)
plt.colorbar()
plt.title("Spline Interpolasyonu")
plt.show()

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

# UnivariateSpline İle Nesne Yönelimli Spline İnterpolasyonu #

Python'da spline interpolasyonu için nesne yönelimli (ing. object oriented) bir alternatif de bulunmaktadır. Bu alternatifte başlatıcı <i>(__init__)</i> metodunaa $(x,y)$ verisi geçirilerek bir $spline$ nesnesi oluşturulur. Sınıfın <i>__call__</i> metodu gönderilen $x$ değerleri için <i>spline interpolasyonu</i> ile y değerlerini hesaplar ve döndürür. `InterpolatedUnivariateSpline` alt sınıfı bu işlemi yapmasının yanı sıra ayrıca integral, türev ve kök bulma için de metodlara sahiptir.

Bunun yanı sıra düzleştirme istendiğinde tıpkı yapısal alternatifte olduğu gibi $s$ parametresi kullanılır. Bu durumda verideki düğüm sayısından daha az (düzleştirme miktarı kadar az) düğüm içeren bir spline fonksiyonu oluşturulur. Bu şekilde düzleştirme kullanılarak oluşturulan spline fonksiyonuna  <i>“interpole spline”</i> yerine <i>“düzleştirilmiş spline”</i> adı verilir.

`UnivariateSpline` sınıfının bir başka alt sınıfı olan `LSQUnivariateSpline` $t$ parametresi ile düğümleri dışarıdan yerleri ile birlikte sağlamak için kullanılabilir. Aralarında eşit uzaklıklar olmayan ve her noktadan geçmeyen; bazı aralıklarda düzleştirme içeren bazılarında içermeyen özel nitelikli spline fonksiyonları yaratmak için kullanışlıdır.

Şimdi bir önceki örnekte yapısal yöntemle gerçekleştirdiğimizi interpolasyonu bir de nesne yönelimli yöntemle gerçekleştirelim.

In [ ]:
x = np.arange(0, 2*np.pi+np.pi/4, 2*np.pi/8)
y = np.sin(x)
s = interpolate.InterpolatedUnivariateSpline(x, y)
xyeni = np.arange(0, 2*np.pi, np.pi/50)
yyeni = s(xyeni)
plt.plot(x,y,'g-',label="veri")
plt.plot(xyeni,yyeni,'b-',label="Kubik spline")
plt.legend(loc="upper right")
plt.axis([-0.05, 6.33, -1.05, 1.05])
plt.title('Kubik Spline (Nesne Yonelimli) Interpolasyonu')
plt.show()

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

# Örnek: Spline Fonksiyonları ile İnterpolasyon #

<i>Spline fonksiyonlarında</i> türev, integral ve kök bulmaya yönelik genel bir örnek aşağıdaki kodla verilmektedir. Koda ilişkin açıklamalar iç dokümatasyonda "#" ile sınırlanan yorum ifadeleri ile kod içinden sağlanmıştır.

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from scipy import interpolate

# Kubik Spline

x = np.arange(0, 2*np.pi+np.pi/4, 2*np.pi/8)
y = np.sin(x)
tck = interpolate.splrep(x, y, s=0)
xyeni = np.arange(0, 2*np.pi, np.pi/50)
yyeni = interpolate.splev(xyeni, tck, der=0)

# Grafik
plt.figure()
plt.plot(x, y, 'x', xyeni, yyeni, xyeni, np.sin(xyeni), x, y, 'b')
plt.legend(['Dogrusal', 'Kubik Spline', 'Veri'])
plt.axis([-0.05, 6.33, -1.05, 1.05])
plt.title('Kubik Spline Interpolasyonu')
plt.show()

# Turevi
yturev = interpolate.splev(xyeni, tck, der=1)
plt.figure()
plt.plot(xyeni, yturev, xyeni, np.cos(xyeni),'--')
plt.legend(['Kubik Spline', 'Veri'])
plt.axis([-0.05, 6.33, -1.05, 1.05])
plt.title('Spline Ile Hesaplanan Turev')
plt.show()

# Integrali
def integ(x, tck, constant=-1):
    x = np.atleast_1d(x)
    sonuc = np.zeros(x.shape, dtype=x.dtype)
    for n in range(len(sonuc)):
        sonuc[n] = interpolate.splint(0, x[n], tck)
    sonuc += constant
    return sonuc

yint = integ(xyeni, tck)
plt.figure()
plt.plot(xyeni, yint, xyeni, -np.cos(xyeni), '--')
plt.legend(['Kubik Spline', 'Veri'])
plt.axis([-0.05, 6.33, -1.05, 1.05])
plt.title('Spline Ile Hesaplanan Integral')
plt.show()

# Kokleri
interpolate.sproot(tck)
# array([3.1416])

# sproot fonksiyonunun x = 0 kokunu bulamadigina dikkat ediniz!
# bu koku bulabilmek icin spline'i daha genis bir aralik uzerinden
# hesaplamaniz gerekir!
x = np.linspace(-np.pi/4, 2.*np.pi + np.pi/4, 21)
y = np.sin(x)
tck = interpolate.splrep(x, y, s=0)
interpolate.sproot(tck)
# array([0., 3.1416])

# Parametrik Spline
t = np.arange(0, 1.1, .1)
x = np.sin(2*np.pi*t)
y = np.cos(2*np.pi*t)
tck, u = interpolate.splprep([x, y], s=0)
uyeni = np.arange(0, 1.01, 0.01)
cikti = interpolate.splev(uyeni, tck)
plt.figure()
plt.plot(x, y, 'x', cikti[0], cikti[1], np.sin(2*np.pi*uyeni), \
         np.cos(2*np.pi*uyeni), x, y, 'b')
plt.legend(['Dogrusal', 'Kubik Spline', 'Veri'])
plt.axis([-1.05, 1.05, -1.05, 1.05])
plt.title('Parametrik Veri icin Spline')
plt.show()

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

# Kaynaklar #

* Data Reduction and Error Analysis for the Physical Sciences, 3rd ed., Philip R.Bevington & D. Keith Robinson, 2003, McGraw Hill Higher Education

* [scipy.interpolate Dokümantasyonu](https://docs.scipy.org/doc/scipy/reference/interpolate.html)

* Tanımlar için: [wikipedia Interpolasyon başlığı](https://en.wikipedia.org/wiki/Interpolation)

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)